# Question: How can we tell if someone can be trusted or not?

In [1]:
import pandas as pd
import numpy as np

In [2]:
accepted_df = pd.read_csv("Sample Datasets/Lending Club/accepted.csv")
rejected_df = pd.read_csv("Sample Datasets/Lending Club/rejected.csv")
accepted_df_org = accepted_df.copy()
rejected_df_org = rejected_df.copy()

C:\Users\mowai\AppData\Local\Temp\ipykernel_30620\3352672681.py:1: DtypeWarning: Columns (20) have mixed types. Specify dtype option on import or set low_memory=False.
  accepted_df = pd.read_csv("Sample Datasets/Lending Club/accepted.csv")


# Preprocessing

In [3]:
for idx,row in accepted_df.iterrows():
    if(row["last_fico_range_low"]==0.0):
        accepted_df["last_fico_range_low"][idx] = row["fico_range_low"]
        accepted_df["last_fico_range_high"][idx] = row["fico_range_high"]

C:\Users\mowai\AppData\Local\Temp\ipykernel_30620\1683451651.py:3: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  accepted_df["last_fico_range_low"][idx] = row["fico_range_low"]
C:\Users\mowai\AppData\Local\Temp\ipykernel_30620\1683451651.py:

In [4]:
(accepted_df["last_fico_range_high"] - accepted_df["last_fico_range_low"]).value_counts()

4.0    99979
5.0       21
Name: count, dtype: int64

### Which factors matter the most to determine if a loan is paid off most

In [5]:
accepted_df["loan_status"].value_counts()

loan_status
Fully Paid            70288
Charged Off           17603
Current               11402
Late (31-120 days)      441
In Grace Period         199
Late (16-30 days)        66
Default                   1
Name: count, dtype: int64

In [6]:
# we are going to remove loan_status=current and combine the late customers.
df_no_current_payers = accepted_df[(accepted_df["loan_status"]!="Default") & (accepted_df["loan_status"]!="Current")]
df_no_current_payers["loan_status"].value_counts()

loan_status
Fully Paid            70288
Charged Off           17603
Late (31-120 days)      441
In Grace Period         199
Late (16-30 days)        66
Name: count, dtype: int64

In [7]:
from sklearn.tree import DecisionTreeClassifier
tree = DecisionTreeClassifier()

In [8]:
# Format the data
X = df_no_current_payers.drop("loan_status",axis=1).to_numpy()
y = df_no_current_payers["loan_status"].to_numpy()
print(X.shape,y.shape)

(88597, 151) (88597,)


emp_title 5674
emp_length 5653
url (just remove)
desc(remove)
purpose (remove)
title (remove)
zip_code (remove)
last_pymnt_d 71
next_pymnt_d 87891
verification_status_joint 88201
hardship_reason 87987
hardship_type 87987
hardship_start_date 87987
hardship_end_date 87987
payment_plan_start_date 87987
hardship_loan_status 87987
disbursement_method 0
debt_settlement_flag 0
debt_settlement_flag_date 85649
settlement_status 85649
settlement_date 85649

In [9]:
df_no_current_payers_float = df_no_current_payers.select_dtypes(include=["float"])
df_no_current_payers_float.head(5)

member_id  loan_amnt  funded_amnt  funded_amnt_inv  int_rate  installment  \
0        NaN     3600.0       3600.0           3600.0     13.99       123.03   
1        NaN    24700.0      24700.0          24700.0     11.99       820.28   
2        NaN    20000.0      20000.0          20000.0     10.78       432.66   
4        NaN    10400.0      10400.0          10400.0     22.45       289.91   
5        NaN    11950.0      11950.0          11950.0     13.44       405.18   

   annual_inc    dti  delinq_2yrs  fico_range_low  ...  deferral_term  \
0     55000.0   5.91          0.0           675.0  ...            NaN   
1     65000.0  16.06          1.0           715.0  ...            NaN   
2     63000.0  10.78          0.0           695.0  ...            NaN   
4    104433.0  25.37          1.0           695.0  ...            NaN   
5     34000.0  10.20          0.0           690.0  ...            NaN   

   hardship_amount  hardship_length  hardship_dpd  \
0              NaN              NaN           NaN   
1              NaN              NaN           NaN   
2              NaN              NaN           NaN   
4              NaN              NaN           NaN   
5              NaN              NaN           NaN   

   orig_projected_additional_accrued_interest  hardship_payoff_balance_amount  \
0                                         NaN                             NaN   
1                                         NaN                             NaN   
2                                         NaN                             NaN   
4                                         NaN                             NaN   
5                                         NaN                             NaN   

   hardship_last_payment_amount  settlement_amount  settlement_percentage  \
0                           NaN                NaN                    NaN   
1                           NaN                NaN                    NaN   
2                           NaN                NaN                    NaN   
4                           NaN                NaN                    NaN   
5                           NaN                NaN                    NaN   

   settlement_term  
0              NaN  
1              NaN  
2              NaN  
4              NaN  
5              NaN  

[5 rows x 114 columns]

In [10]:
# remove all columns which have missing values above 10K (10% of 100K)
columns_to_remove = [(k) for k,v in df_no_current_payers_float.isnull().sum().items() if v>10000]
df_no_current_payers_float = df_no_current_payers_float.drop(columns=columns_to_remove,axis=1)

In [11]:
# impute remaining null containing columns
[[k,v] for k,v in df_no_current_payers_float.isnull().sum().items() if v>0]

[['dti', 2],
 ['revol_util', 36],
 ['bc_open_to_buy', 905],
 ['bc_util', 953],
 ['mo_sin_old_il_acct', 2571],
 ['mths_since_recent_bc', 867],
 ['mths_since_recent_inq', 9320],
 ['num_rev_accts', 1],
 ['num_tl_120dpd_2m', 4628],
 ['percent_bc_gt_75', 980]]

In [12]:
df_no_current_payers_float["bc_util"].unique()

array([ 37.2,  27.1,  55.9, ..., 122.6, 125.1, 109.6])

In [13]:
from sklearn.preprocessing import OneHotEncoder

In [14]:
df_no_current_payers_float["dti"] = df_no_current_payers_float["dti"].fillna(round(df_no_current_payers_float["dti"].mean(),1))
df_no_current_payers_float["revol_util"] = df_no_current_payers_float["revol_util"].fillna(round(df_no_current_payers_float["revol_util"].mean(),1))
df_no_current_payers_float["bc_open_to_buy"] = df_no_current_payers_float["bc_open_to_buy"].fillna(round(df_no_current_payers_float["bc_open_to_buy"].mean(),1))
df_no_current_payers_float["mo_sin_old_il_acct"] = df_no_current_payers_float["mo_sin_old_il_acct"].fillna(round(df_no_current_payers_float["mo_sin_old_il_acct"].mean(),0))
df_no_current_payers_float["mths_since_recent_bc"] = df_no_current_payers_float["mths_since_recent_bc"].fillna(round(df_no_current_payers_float["mths_since_recent_bc"].mean(),0))
df_no_current_payers_float["mths_since_recent_inq"] = df_no_current_payers_float["mths_since_recent_inq"].fillna(round(df_no_current_payers_float["mths_since_recent_inq"].mean(),0))
df_no_current_payers_float["num_rev_accts"] = df_no_current_payers_float["num_rev_accts"].fillna(round(df_no_current_payers_float["num_rev_accts"].mean(),0))
df_no_current_payers_float["num_tl_120dpd_2m"] = df_no_current_payers_float["num_tl_120dpd_2m"].fillna(round(df_no_current_payers_float["num_tl_120dpd_2m"].mean(),0))
df_no_current_payers_float["percent_bc_gt_75"] = df_no_current_payers_float["percent_bc_gt_75"].fillna(round(df_no_current_payers_float["percent_bc_gt_75"].mean(),1))
df_no_current_payers_float["bc_util"] = df_no_current_payers_float["bc_util"].fillna(round(df_no_current_payers_float["bc_util"].mean(),1))

In [15]:
simplified_target_col = df_no_current_payers["loan_status"].replace(['Late (31-120 days)', 'Late (16-30 days)'], 'Late')
encoder = OneHotEncoder()
encoded_target_col = encoder.fit_transform(pd.DataFrame({"y":simplified_target_col}))
y = encoded_target_col.toarray()
y = (np.argmax(y, axis=1) + 1)

In [16]:
X = df_no_current_payers_float.to_numpy()
print(X.shape,y.shape)

(88597, 69) (88597,)


In [17]:
tree.fit(X,y)

DecisionTreeClassifier()

In [18]:
# plot float feature importance
importance = tree.feature_importances_

In [19]:
import plotly.express as px

fig = px.bar(x=df_no_current_payers_float.columns,y=importance,title="Feature Importance for Numerical columns")
fig.show()

In [20]:
feature_importances = dict(zip(df_no_current_payers_float.columns,importance))

In [21]:
feature_importances_sorted = dict(sorted(feature_importances.items(),key=lambda item:item[1],reverse=True))

In [22]:
feature_importances2 = feature_importances.copy()


In [23]:
del feature_importances2["recoveries"]

In [24]:
fig2 = px.bar(x=list(feature_importances_sorted.keys()),y=list(feature_importances_sorted.values()))
fig2.show()

In [25]:
# checking values for recoveries by loan status
print(accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["recoveries"].unique())
print(accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["recoveries"].unique())
print(accepted_df[accepted_df["loan_status"]=="Fully Paid"]["recoveries"].unique())
print(accepted_df[accepted_df["loan_status"]=="In Grace Period"]["recoveries"].unique())
print(accepted_df[accepted_df["loan_status"]=="Charged Off"]["recoveries"].unique())

[0.]
[0.]
[0.]
[0.]
[1618.9   368.37    0.   ... 2008.    861.43 1584.98]


As we can see above, only loans charged off have recoveries

In [26]:
print("Late (31-120 days) average = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_fico_range_low"].mean())
print("Late (31-120 days) minimum = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_fico_range_low"].min())
print("Late (31-120 days) maximum = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_fico_range_low"].max())
print("Late (16-30 days) average = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_fico_range_low"].mean())
print("Late (16-30 days) minimum = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_fico_range_low"].min())
print("Late (16-30 days) maximum = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_fico_range_low"].max())
print("Fully Paid average = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_fico_range_low"].mean())
print("Fully Paid minimum = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_fico_range_low"].min())
print("Fully Paid maximum = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_fico_range_low"].max())
print("In Grace Period average = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_fico_range_low"].mean())
print("In Grace Period minimum = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_fico_range_low"].min())
print("In Grace Period maximum = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_fico_range_low"].max())
print("Charged Off average = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_fico_range_low"].mean())
print("Charged Off minimum = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_fico_range_low"].min())
print("Charged Off maximum = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_fico_range_low"].max())
print("Current average = ",accepted_df[accepted_df["loan_status"]=="Current"]["last_fico_range_low"].mean())
print("Current minimum = ",accepted_df[accepted_df["loan_status"]=="Current"]["last_fico_range_low"].min())
print("Current maximum = ",accepted_df[accepted_df["loan_status"]=="Current"]["last_fico_range_low"].max())

Late (31-120 days) average =  593.764172335601
Late (31-120 days) minimum =  500.0
Late (31-120 days) maximum =  780.0
Late (16-30 days) average =  627.6515151515151
Late (16-30 days) minimum =  540.0
Late (16-30 days) maximum =  725.0
Fully Paid average =  701.4071391987252
Fully Paid minimum =  500.0
Fully Paid maximum =  845.0
In Grace Period average =  643.0402010050251
In Grace Period minimum =  500.0
In Grace Period maximum =  810.0
Charged Off average =  582.2720558995626
Charged Off minimum =  500.0
Charged Off maximum =  830.0
Current average =  693.5796351517278
Current minimum =  500.0
Current maximum =  845.0


In [27]:
print("Late (31-120 days) average = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["fico_range_low"].mean())
print("Late (31-120 days) minimum = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["fico_range_low"].min())
print("Late (31-120 days) maximum = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["fico_range_low"].max())
print("Late (16-30 days) average = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["fico_range_low"].mean())
print("Late (16-30 days) minimum = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["fico_range_low"].min())
print("Late (16-30 days) maximum = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["fico_range_low"].max())
print("Fully Paid average = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["fico_range_low"].mean())
print("Fully Paid minimum = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["fico_range_low"].min())
print("Fully Paid maximum = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["fico_range_low"].max())
print("In Grace Period average = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["fico_range_low"].mean())
print("In Grace Period minimum = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["fico_range_low"].min())
print("In Grace Period maximum = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["fico_range_low"].max())
print("Charged Off average = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["fico_range_low"].mean())
print("Charged Off minimum = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["fico_range_low"].min())
print("Charged Off maximum = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["fico_range_low"].max())
print("Current average = ",accepted_df[accepted_df["loan_status"]=="Current"]["fico_range_low"].mean())
print("Current minimum = ",accepted_df[accepted_df["loan_status"]=="Current"]["fico_range_low"].min())
print("Current maximum = ",accepted_df[accepted_df["loan_status"]=="Current"]["fico_range_low"].max())


Late (31-120 days) average =  685.8049886621316
Late (31-120 days) minimum =  660.0
Late (31-120 days) maximum =  795.0
Late (16-30 days) average =  687.6515151515151
Late (16-30 days) minimum =  660.0
Late (16-30 days) maximum =  765.0
Fully Paid average =  696.6141446619622
Fully Paid minimum =  660.0
Fully Paid maximum =  845.0
In Grace Period average =  691.3819095477387
In Grace Period minimum =  660.0
In Grace Period maximum =  805.0
Charged Off average =  686.1472476282452
Charged Off minimum =  660.0
Charged Off maximum =  845.0
Current average =  695.6086651464656
Current minimum =  660.0
Current maximum =  835.0


In [28]:
print("Late (31-120 days) average = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_fico_range_high"].mean())
print("Late (31-120 days) minimum = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_fico_range_high"].min())
print("Late (31-120 days) maximum = ",accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_fico_range_high"].max())
print("Late (16-30 days) average = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_fico_range_high"].mean())
print("Late (16-30 days) minimum = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_fico_range_high"].min())
print("Late (16-30 days) maximum = ",accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_fico_range_high"].max())
print("Fully Paid average = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_fico_range_high"].mean())
print("Fully Paid minimum = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_fico_range_high"].min())
print("Fully Paid maximum = ",accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_fico_range_high"].max())
print("In Grace Period average = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_fico_range_high"].mean())
print("In Grace Period minimum = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_fico_range_high"].min())
print("In Grace Period maximum = ",accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_fico_range_high"].max())
print("Charged Off average = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_fico_range_high"].mean())
print("Charged Off minimum = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_fico_range_high"].min())
print("Charged Off maximum = ",accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_fico_range_high"].max())
print("Current average = ",accepted_df[accepted_df["loan_status"]=="Current"]["last_fico_range_high"].mean())
print("Current minimum = ",accepted_df[accepted_df["loan_status"]=="Current"]["last_fico_range_high"].min())
print("Current maximum = ",accepted_df[accepted_df["loan_status"]=="Current"]["last_fico_range_high"].max())


Late (31-120 days) average =  597.764172335601
Late (31-120 days) minimum =  504.0
Late (31-120 days) maximum =  784.0
Late (16-30 days) average =  631.6515151515151
Late (16-30 days) minimum =  544.0
Late (16-30 days) maximum =  729.0
Fully Paid average =  705.4074095151377
Fully Paid minimum =  504.0
Fully Paid maximum =  850.0
In Grace Period average =  647.0402010050251
In Grace Period minimum =  504.0
In Grace Period maximum =  814.0
Charged Off average =  586.2720558995626
Charged Off minimum =  504.0
Charged Off maximum =  834.0
Current average =  697.579810559551
Current minimum =  504.0
Current maximum =  850.0


In [29]:

print(accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["total_rec_prncp"].mean())
print(accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["total_rec_prncp"].mean())
print(accepted_df[accepted_df["loan_status"]=="Fully Paid"]["total_rec_prncp"].mean())
print(accepted_df[accepted_df["loan_status"]=="In Grace Period"]["total_rec_prncp"].mean())
print(accepted_df[accepted_df["loan_status"]=="Charged Off"]["total_rec_prncp"].mean())

10488.150702947845
10396.130151515152
14065.021766162077
11767.431005025124
4722.198076464239


Total received principal is lower for charged off and late deliveries, that is obvious

In [30]:
print(accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_pymnt_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["last_pymnt_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_pymnt_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="In Grace Period"]["last_pymnt_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="Charged Off"]["last_pymnt_amnt"].mean())


473.24941043083896
504.89
5739.212072330982
602.2621105527637
452.45432539907966


In [31]:
print(accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["last_pymnt_amnt"].nlargest(5))
print(accepted_df[accepted_df["loan_status"]=="Fully Paid"]["last_pymnt_amnt"].nlargest(5))

49445    3631.39
83396    2500.00
37952    2495.36
2089     1978.00
48086    1805.25
Name: last_pymnt_amnt, dtype: float64
36854    36307.01
55911    36192.86
34665    36159.30
3367     36127.51
26749    36069.62
Name: last_pymnt_amnt, dtype: float64


The last paid amounts are big for the FUlly paid loans showing us that borrowers pay the largest installment at the end.

In [32]:
print(accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["funded_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["funded_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="Fully Paid"]["funded_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="In Grace Period"]["funded_amnt"].mean())
print(accepted_df[accepted_df["loan_status"]=="Charged Off"]["funded_amnt"].mean())



18700.96371882086
18833.71212121212
14065.021767584794
20337.562814070352
15618.175879111515


In [33]:

print(accepted_df[accepted_df["loan_status"]=="Late (31-120 days)"]["installment"].mean())
print(accepted_df[accepted_df["loan_status"]=="Late (16-30 days)"]["installment"].mean())
print(accepted_df[accepted_df["loan_status"]=="Fully Paid"]["installment"].mean())
print(accepted_df[accepted_df["loan_status"]=="In Grace Period"]["installment"].mean())
print(accepted_df[accepted_df["loan_status"]=="Charged Off"]["installment"].mean())

468.96022675736964
456.5375757575758
424.7056935750057
496.9839698492462
450.2328835993864


## Conclusion:
As we can see, the fico score is very important when assessing borrower creditibility

In [34]:
# emp length
# homeownership
# earliest crline
# verficiation status
# hardship plan 

# Association between Personal details and Borrower creditbility

THe factors we will be looking at are:
Employment length
Income Verification status 
Home ownership
Earliest credit line opened
Existence of a co borrower

## Data Exploration (emp_length)

In [35]:
print(accepted_df["emp_length"].value_counts())
print(accepted_df["emp_length"].isna().sum())

emp_length
10+ years    33591
< 1 year      8765
2 years       8706
3 years       8063
1 year        6507
5 years       5997
4 years       5726
8 years       5081
6 years       3876
9 years       3851
7 years       3725
Name: count, dtype: int64
6112


A large proportion of our clients are older

In [36]:
df2 = accepted_df.copy()
df2["emp_length"] = accepted_df["emp_length"].fillna("N/A")

In [37]:
px.pie(df2["emp_length"].value_counts().reset_index(),names="emp_length",values="count",title="Employment length proportion")

this is also a point of concern, some people may be lying to us to secure a loan

## EDA (Home ownership)

In [38]:
print(accepted_df["home_ownership"].value_counts())
print(accepted_df["home_ownership"].isna().sum())

home_ownership
MORTGAGE    49477
RENT        39257
OWN         11265
ANY             1
Name: count, dtype: int64
0


In [39]:
df2["home_ownership"] = df2["home_ownership"].replace("ANY","MORTGAGE")
df2["home_ownership"].value_counts()

home_ownership
MORTGAGE    49478
RENT        39257
OWN         11265
Name: count, dtype: int64

In [40]:
px.pie(df2["home_ownership"].value_counts().reset_index(),names="home_ownership",values="count",title="Employment length proportion")

In [41]:
from datetime import datetime

def is_valid_month_year(date_str):
    try:
        datetime.strptime(date_str, "%b-%Y")
        return True
    except ValueError:
        return False

In [42]:
df2['earliest_cr_line'].apply(is_valid_month_year).sum() # check format

100000

In [43]:
df2["verification_status"].value_counts()

verification_status
Source Verified    42260
Verified           31798
Not Verified       25942
Name: count, dtype: int64

In [44]:
print(df2[df2["hardship_type"].notna()]["hardship_type"].unique())
print(df2[df2["hardship_reason"].notna()]["hardship_reason"].unique())
print(df2["hardship_flag"].value_counts())

# Lets not use hardship as there are not many values

['INTEREST ONLY-3 MONTHS DEFERRAL']
['NATURAL_DISASTER' 'DIVORCE' 'EXCESSIVE_OBLIGATIONS' 'DISABILITY'
 'UNEMPLOYMENT' 'INCOME_CURTAILMENT' 'REDUCED_HOURS' 'MEDICAL'
 'FAMILY_DEATH']
hardship_flag
N    99980
Y       20
Name: count, dtype: int64


## Employment length Analysis

In [45]:
df2["loan_status"].unique()

array(['Fully Paid', 'Current', 'Charged Off', 'In Grace Period',
       'Late (31-120 days)', 'Late (16-30 days)', 'Default'], dtype=object)

In [46]:
count = df2.groupby(["emp_length","loan_status"]).size().reset_index(name="count")
count

emp_length         loan_status  count
0      1 year         Charged Off   1216
1      1 year             Current    678
2      1 year          Fully Paid   4571
3      1 year     In Grace Period      7
4      1 year   Late (16-30 days)      6
..        ...                 ...    ...
68        N/A             Current    459
69        N/A          Fully Paid   4203
70        N/A     In Grace Period      5
71        N/A   Late (16-30 days)      1
72        N/A  Late (31-120 days)     18

[73 rows x 3 columns]

In [47]:
totals = count.groupby("emp_length")["count"].transform("sum")

In [48]:
count["proportion"] = count["count"] / totals
count

emp_length         loan_status  count  proportion
0      1 year         Charged Off   1216    0.186876
1      1 year             Current    678    0.104195
2      1 year          Fully Paid   4571    0.702474
3      1 year     In Grace Period      7    0.001076
4      1 year   Late (16-30 days)      6    0.000922
..        ...                 ...    ...         ...
68        N/A             Current    459    0.075098
69        N/A          Fully Paid   4203    0.687664
70        N/A     In Grace Period      5    0.000818
71        N/A   Late (16-30 days)      1    0.000164
72        N/A  Late (31-120 days)     18    0.002945

[73 rows x 4 columns]

In [49]:
fig = px.bar(count,x="emp_length",y="count",color="loan_status",text=count['proportion'].apply(lambda x: f'{x:.0%}'),title="Number of employees by Loan status and employment type ")
fig.update_traces(textposition='inside')
fig.update_layout(barmode='stack', yaxis_title='proportion', )
fig.show()

In [50]:

fig = px.bar(count,x="emp_length",y="proportion",color="loan_status",text=count['proportion'].apply(lambda x: f'{x:.0%}'),title="Proportion of employees by Loan status and employment type ")
fig.update_traces(textposition='inside')
fig.update_layout(barmode='stack', yaxis_title='proportion', )
fig.show()

Surprisingly, the fully paid payments are of equal proportion for all types of employees.
However, there is a small chance that people who have not provided employment staty are likely not to pay their full loan. Lets now look at how much of a loss they have caused compared to others

In [51]:
# The loss they have caused = loan_amnt - total_pymnt_rec
# the proportion that has been paid - loss we calc/loan_amnt
# how long it took for them to be charged off - 
count

emp_length         loan_status  count  proportion
0      1 year         Charged Off   1216    0.186876
1      1 year             Current    678    0.104195
2      1 year          Fully Paid   4571    0.702474
3      1 year     In Grace Period      7    0.001076
4      1 year   Late (16-30 days)      6    0.000922
..        ...                 ...    ...         ...
68        N/A             Current    459    0.075098
69        N/A          Fully Paid   4203    0.687664
70        N/A     In Grace Period      5    0.000818
71        N/A   Late (16-30 days)      1    0.000164
72        N/A  Late (31-120 days)     18    0.002945

[73 rows x 4 columns]

In [52]:
df2["total_rec"]

KeyError: 'total_rec'

In [ ]:
losses = df2[["emp_length","loan_status","loan_amnt","total_pymnt","total_rec_int","total_rec_late_fee"]]

In [ ]:
losses["loss"] = losses["loan_amnt"] - (losses["total_pymnt"] - losses["total_rec_int"] - losses["total_rec_late_fee"])

C:\Users\mowai\AppData\Local\Temp\ipykernel_4104\1240541114.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
losses = losses[losses["loan_status"]=="Charged Off"]

-1483.5600000000013

In [ ]:
total_losses = losses.groupby("emp_length")["loss"].sum()
total_losses = total_losses.reset_index()
total_losses

emp_length          loss
0      1 year  1.099414e+07
1   10+ years  5.688051e+07
2     2 years  1.443467e+07
3     3 years  1.386866e+07
4     4 years  9.762730e+06
5     5 years  1.075331e+07
6     6 years  6.502171e+06
7     7 years  6.191438e+06
8     8 years  8.920801e+06
9     9 years  6.866016e+06
10   < 1 year  1.527212e+07
11        N/A  9.335214e+06

In [ ]:
fig = px.bar(total_losses,x="emp_length",y="loss",title="Total loss by Employment Length ",text=total_losses["loss"].apply(lambda x: f'{x:,.0f}'))
fig.show()

In [ ]:
avg_losses = losses.groupby("emp_length")["loss"].mean()
avg_losses = avg_losses.reset_index()
avg_losses

emp_length          loss
0      1 year   9041.229951
1   10+ years  10541.235669
2     2 years   9428.263688
3     3 years   9571.192043
4     4 years   9599.537876
5     5 years   9920.024862
6     6 years   9881.718283
7     7 years   9874.701435
8     8 years   9978.524497
9     9 years   9766.736430
10   < 1 year   9533.157129
11        N/A   6546.433345

In [ ]:
fig = px.bar(avg_losses,x="emp_length",y="loss",title="Average loss by Employment Length ",text=avg_losses["loss"].apply(lambda x: f'{x:,.0f}'))
fig.show()

In [ ]:
fig = px.box(losses,x="emp_length",y="loss",title="Loss distribution by Employee types")
fig.show()

In [ ]:
def count_outliers(group):
    q1 = group.quantile(0.25)
    q3 = group.quantile(0.75)
    iqr = q3 - q1
    lower = q1 - 1.5 * iqr
    upper = q3 + 1.5 * iqr
    return ((group < lower) | (group > upper)).sum()

outlier_counts = losses.groupby('emp_length')['loss'].apply(count_outliers).reset_index()
outlier_counts.columns = ['emp_length', 'outlier_count']

print(outlier_counts)

   emp_length  outlier_count
0      1 year             26
1   10+ years             35
2     2 years             32
3     3 years             25
4     4 years             11
5     5 years             10
6     6 years             10
7     7 years              9
8     8 years             12
9     9 years             11
10   < 1 year             31
11        N/A             41


In [ ]:
px.bar(outlier_counts,x="emp_length",y="outlier_count",text="outlier_count",title="Number of extremely high loans by type of Employee")

In [ ]:
employee_type_counts = df2["emp_length"].value_counts().reset_index()
employee_type_counts["proportion"] = outlier_counts["outlier_count"] / employee_type_counts["count"]
employee_type_counts

emp_length  count  proportion
0   10+ years  33591    0.000774
1    < 1 year   8765    0.003993
2     2 years   8706    0.003676
3     3 years   8063    0.003101
4      1 year   6507    0.001690
5         N/A   6112    0.001636
6     5 years   5997    0.001668
7     4 years   5726    0.001572
8     8 years   5081    0.002362
9     6 years   3876    0.002838
10    9 years   3851    0.008050
11    7 years   3725    0.011007

In [ ]:
px.bar(outlier_counts,x="emp_length",y=employee_type_counts["proportion"],text=employee_type_counts["proportion"].apply(lambda x: f'{x:.2%}')
       ,title="Number of extremely high loans by type of Employee")

We have found something quite interesting regarding the link between our customers employment and if they are likely to pay back:
1. Employees with more than 10 years of employment are incredibly high, way more than employees with 9 years of employment, this can indicate that they are fabricating their employment data, I need to check if they have been verified. I also need to check if they are fabricating other financial data.
2. When it comes to how likely someone is not to pay their loan, people who have not provided their financial data have the highest probability at 23%
3. However, when we look at the actual loss caused to us, it is people who have told us they were employed for 10+ years that have caused us the highest average loss although not significant.
4. I decided to look at the medians too to rule out outliers, 10+ years employees still cause the highest loss and get this, they have number of people with extremely high accepted loans that have not been paid back. Although it is only 1.4% of people, it is still the second highest, preceded by people without employment data.

# Verification status analysis

In [ ]:
px.pie(accepted_df["verification_status"].value_counts().reset_index(),names="verification_status",values="count",title="Proportion of Verification Status")

In [ ]:
verification_count = df2.groupby(["emp_length","verification_status"]).size().reset_index(name="count")
totals = verification_count.groupby("emp_length")["count"].transform("sum")
verification_count["proportion"] = verification_count["count"] / totals
verification_count

emp_length verification_status  count  proportion
0      1 year        Not Verified   1580    0.242815
1      1 year     Source Verified   3084    0.473951
2      1 year            Verified   1843    0.283233
3   10+ years        Not Verified   9321    0.277485
4   10+ years     Source Verified  13994    0.416600
5   10+ years            Verified  10276    0.305915
6     2 years        Not Verified   2126    0.244199
7     2 years     Source Verified   4112    0.472318
8     2 years            Verified   2468    0.283483
9     3 years        Not Verified   2006    0.248791
10    3 years     Source Verified   3673    0.455538
11    3 years            Verified   2384    0.295672
12    4 years        Not Verified   1399    0.244324
13    4 years     Source Verified   2591    0.452497
14    4 years            Verified   1736    0.303178
15    5 years        Not Verified   1547    0.257962
16    5 years     Source Verified   2632    0.438886
17    5 years            Verified   1818    0.303152
18    6 years        Not Verified   1030    0.265738
19    6 years     Source Verified   1651    0.425955
20    6 years            Verified   1195    0.308308
21    7 years        Not Verified    977    0.262282
22    7 years     Source Verified   1585    0.425503
23    7 years            Verified   1163    0.312215
24    8 years        Not Verified   1333    0.262350
25    8 years     Source Verified   2186    0.430230
26    8 years            Verified   1562    0.307420
27    9 years        Not Verified   1010    0.262270
28    9 years     Source Verified   1614    0.419112
29    9 years            Verified   1227    0.318619
30   < 1 year        Not Verified   2084    0.237764
31   < 1 year     Source Verified   4110    0.468910
32   < 1 year            Verified   2571    0.293326
33        N/A        Not Verified   1529    0.250164
34        N/A     Source Verified   1028    0.168194
35        N/A            Verified   3555    0.581643

In [ ]:
fig = px.bar(verification_count,x="emp_length",y="count",color="verification_status",text=verification_count['proportion'].apply(lambda x: f'{x:.0%}'),title="Number of employees by Loan status and employment type ")
fig.update_traces(textposition='inside')
fig.update_layout(barmode='stack', yaxis_title='proportion', )
fig.show()

In [ ]:
fig = px.bar(verification_count,x="emp_length",y="proportion",color="verification_status",text=verification_count['proportion'].apply(lambda x: f'{x:.0%}'),title="Proportion of employees by Loan status and employment type ")
fig.update_traces(textposition='inside')
fig.update_layout(barmode='stack', yaxis_title='proportion', )
fig.show()

In [ ]:
df3 = accepted_df[accepted_df["loan_status"]=="Charged Off"]
df3["loss"] = losses["loss"]

C:\Users\mowai\AppData\Local\Temp\ipykernel_4104\912136680.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
def remove_iqr_outliers(df, column):
    q1 = df[column].quantile(0.25)
    q3 = df[column].quantile(0.75)
    iqr = q3 - q1
    lower_bound = q1 - 1.5 * iqr
    upper_bound = q3 + 1.5 * iqr
    # Keep only rows within bounds
    return df[(df[column] < lower_bound) | (df[column] > upper_bound)]


In [ ]:
df_outliers = remove_iqr_outliers(df3,"loss")

In [ ]:
df3["ve"]

In [ ]:
df_outliers[["loan_amnt","verification_status"]]

29000.0

In [ ]:
df_outliers["loss"]

1079     31524.57
3088     32461.36
4265     28211.97
4323     28437.44
4749     28726.89
           ...   
99429    28110.38
99436    29351.88
99562    28534.64
99581    29259.33
99801    29124.07
Name: loss, Length: 265, dtype: float64

In [ ]:
fig = px.box(df3,x="verification_status",y="loss",title="Loss distribution by Employee types")
fig.show()

In [ ]:
outlier_counts = df_outliers["verification_status"].reset_index().groupby("verification_status").count().reset_index()

In [ ]:
fig = px.bar(outlier_counts,x="verification_status",y="index",title="Outliers verification status")
fig.show(
    
)

Contrary to our belief, a lot of the charged off borrowers with extremely high loans are actually verified. This can indicate flaws in our verification system

# Home ownership analysis

In [ ]:
df4 = accepted_df.copy()

In [ ]:
df4.loc[df4["home_ownership"]=="ANY"] = "MORTGAGE"


In [ ]:
px.pie(df4["home_ownership"].value_counts().reset_index(),names="home_ownership",values="count",title="Proportion of Home Ownership")

In [ ]:
loan_home_status = df4.groupby(['home_ownership', 'loan_status']).size().reset_index(name='Count')
loan_home_status

home_ownership         loan_status  Count
0        MORTGAGE         Charged Off   7449
1        MORTGAGE             Current   6332
2        MORTGAGE          Fully Paid  35345
3        MORTGAGE     In Grace Period    114
4        MORTGAGE   Late (16-30 days)     28
5        MORTGAGE  Late (31-120 days)    209
6        MORTGAGE            MORTGAGE      1
7             OWN         Charged Off   2068
8             OWN             Current   1216
9             OWN             Default      1
10            OWN          Fully Paid   7911
11            OWN     In Grace Period     11
12            OWN   Late (16-30 days)      8
13            OWN  Late (31-120 days)     50
14           RENT         Charged Off   8086
15           RENT             Current   3854
16           RENT          Fully Paid  27031
17           RENT     In Grace Period     74
18           RENT   Late (16-30 days)     30
19           RENT  Late (31-120 days)    182

In [ ]:
fig = px.sunburst(loan_home_status, path=['loan_status', 'home_ownership'], values='Count', 
                  title='Loan status and Home ownership proportions')
fig.show()

In [ ]:
fig = px.bar(loan_home_status,x="loan_status",y="Count",color="home_ownership",title="Loan Status count grouped by home ownership")
fig.update_layout(barmode='stack', yaxis_title='proportion', )
fig.show()